# Part 3 - Text analysis and ethics

# 3.a Computing PMI

In this assessment you are tasked to discover strong associations between concepts in Airbnb reviews. The starter code we provide in this notebook is for orientation only. The below imports are enough to implement a valid answer.

### Imports, data loading and helper functions

We first connect our google drive, import pandas, numpy and some useful nltk and collections modules, then load the dataframe and define a function for printing the current time, useful to log our progress in some of the tasks.

In [1]:
import pandas as pd
from nltk.tag import pos_tag
from nltk import RegexpParser
import re
from collections import defaultdict,Counter
from nltk.stem import WordNetLemmatizer
from datetime import datetime
from tqdm import tqdm
import numpy as np
import os
tqdm.pandas()

In [2]:
# nltk imports, note that these outputs may be different if you are using colab or local jupyter notebooks
import nltk
nltk.download('stopwords')
nltk.download('punkt')
nltk.download('averaged_perceptron_tagger')
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize,sent_tokenize

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Andreas\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\Andreas\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     C:\Users\Andreas\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


In [3]:
# load stopwords
sw = set(stopwords.words('english'))

In [4]:
# sw

In [5]:
pattern = r'\w+\'\w+'

new_stopwords = []
for word in sw:
    if len(re.findall(pattern,word)) == 1:
        new_stopwords.append(re.findall(pattern,word)[0].replace('\'',''))
# new_stopwords

In [6]:
for word in new_stopwords:
    sw.add(word)
# sw

In [7]:
basedir = os.getcwd()
df = pd.read_csv(os.path.join(basedir,'reviews.csv'))
# deal with empty reviews
df.comments = df.comments.fillna('')

In [8]:
df.head()

listing_id    id        date  reviewer_id reviewer_name  \
0        2818  1191  2009-03-30        10952           Lam   
1        2818  1771  2009-04-24        12798         Alice   
2        2818  1989  2009-05-03        11869       Natalja   
3        2818  2797  2009-05-18        14064       Enrique   
4        2818  3151  2009-05-25        17977       Sherwin   

                                            comments  
0  Daniel is really cool. The place was nice and ...  
1  Daniel is the most amazing host! His place is ...  
2  We had such a great time in Amsterdam. Daniel ...  
3  Very professional operation. Room is very clea...  
4  Daniel is highly recommended.  He provided all...

In [9]:
df.shape

(452143, 6)

### 3.a1 - Process reviews

What to implement: A `function process_reviews(df)` that will take as input the original dataframe and will return it with three additional columns: `tokenized`, `tagged` and `lower_tagged`.

In [10]:
def process_reviews(df):
  tokenized = []
  tagged = []
  lower_tagged = []

  mylen = len(df)
  count = 0
  for index, row in df.iterrows():
    token = word_tokenize(row.comments)
    tokenized.append(token)
    tagged.append(pos_tag(token))
    # lower_tagged.append(list(set(pos_tag([item.lower() for item in token]))))
    lower_tagged.append(pos_tag([item.lower() for item in token if item.lower() not in sw]))
    count += 1
    
    if count % 1000 == 0:
      print(f'{count} out of {mylen}')

  df['tokenized'] = tokenized
  df['tagged'] = tagged
  df['lower_tagged'] = lower_tagged


  # df['tokenized'] = [ word_tokenize(row.comments) for index, row in df.iterrows()]
  # print('Tokenizing done!\n')
  # df['tagged'] = [pos_tag(row.tokenized) for index, row in df.iterrows()]
  # print('Tagging done!\n')
  # df['lower_tagged'] = list(set([pos_tag([item.lower() for item in row.tokenized]) for index, row in df.iterrows()]))
  # print('Lower tagging done!\n')
  return df

In [11]:
df = process_reviews(df[:2000])

1000 out of 10000
2000 out of 10000
3000 out of 10000
4000 out of 10000
5000 out of 10000
6000 out of 10000
7000 out of 10000
8000 out of 10000
9000 out of 10000
10000 out of 10000
<ipython-input-10-54308fc3e191>:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['tokenized'] = tokenized
<ipython-input-10-54308fc3e191>:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['tagged'] = tagged
<ipython-input-10-54308fc3e191>:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a 

In [12]:
df.lower_tagged

0       [(daniel, NN), (really, RB), (cool, JJ), (., ....
1       [(daniel, NN), (amazing, VBG), (host, NN), (!,...
2       [(great, JJ), (time, NN), (amsterdam, NN), (.,...
3       [(professional, JJ), (operation, NN), (., .), ...
4       [(daniel, NN), (highly, RB), (recommended, VBD...
                              ...                        
9995    [(encontrareis, NN), (una, JJ), (casa, NN), (m...
9996    [(great, JJ), (hospitality, NN), (,, ,), (clea...
9997    [(apartment, NN), (centrally, RB), (located, V...
9998    [(location, NN), (studio, NN), (excellent, NN)...
9999    [(owner, NN), (marijn, NNS), (really, RB), (ni...
Name: lower_tagged, Length: 10000, dtype: object

In [13]:
# correction with lower_tagged.append(pos_tag([item.lower() for item in token if item.lower() not in sw]))
lowertagged = []

pattern = r'\w+'

for line in df.lower_tagged:
    print(line)
    for word in line:
        lowertagged.append(word[0])
        # if word[1][0] == 'N' and len(re.findall(pattern,word[0])) == 0: print(word)
        if word[1][0] == 'N': print(word)
            # print(re.findall(pattern,word[0]))
            # if 
lowertagged[:50]

[('daniel', 'NN'), ('really', 'RB'), ('cool', 'JJ'), ('.', '.'), ('place', 'NN'), ('nice', 'JJ'), ('clean', 'NN'), ('.', '.'), ('quiet', 'JJ'), ('neighborhood', 'NN'), ('.', '.'), ('maps', 'NNS'), ('lonely', 'RB'), ('planet', 'JJ'), ('guide', 'NN'), ('book', 'NN'), ('room', 'NN'), ('use', 'NN'), ('.', '.'), ('trouble', 'NN'), ('finding', 'VBG'), ('place', 'JJ'), ('central', 'JJ'), ('station', 'NN'), ('.', '.'), ('would', 'MD'), ('defintely', 'RB'), ('come', 'VB'), ('back', 'RB'), ('!', '.'), ('thanks', 'NNS'), ('!', '.')]
[('daniel', 'NN'), ('amazing', 'VBG'), ('host', 'NN'), ('!', '.'), ('place', 'NN'), ('extremely', 'RB'), ('clean', 'JJ'), (',', ','), ('provides', 'VBZ'), ('everything', 'NN'), ('could', 'MD'), ('possibly', 'RB'), ('want', 'VB'), ('(', '('), ('comfy', 'VB'), ('bed', 'NN'), (',', ','), ('guidebooks', 'VBZ'), ('&', 'CC'), ('maps', 'NNS'), (',', ','), ('mini-fridge', 'NN'), (',', ','), ('towels', 'NNS'), (',', ','), ('even', 'RB'), ('toiletries', 'NNS'), (')', ')'), ('.'

['daniel',
 'really',
 'cool',
 '.',
 'place',
 'nice',
 'clean',
 '.',
 'quiet',
 'neighborhood',
 '.',
 'maps',
 'lonely',
 'planet',
 'guide',
 'book',
 'room',
 'use',
 '.',
 'trouble',
 'finding',
 'place',
 'central',
 'station',
 '.',
 'would',
 'defintely',
 'come',
 'back',
 '!',
 'thanks',
 '!',
 'daniel',
 'amazing',
 'host',
 '!',
 'place',
 'extremely',
 'clean',
 ',',
 'provides',
 'everything',
 'could',
 'possibly',
 'want',
 '(',
 'comfy',
 'bed',
 ',',
 'guidebooks']

In [118]:
df

listing_id         id        date  reviewer_id reviewer_name  \
0           2818       1191  2009-03-30        10952           Lam   
1           2818       1771  2009-04-24        12798         Alice   
2           2818       1989  2009-05-03        11869       Natalja   
3           2818       2797  2009-05-18        14064       Enrique   
4           2818       3151  2009-05-25        17977       Sherwin   
...          ...        ...         ...          ...           ...   
9995      189754  574525848  2019-12-08    273749738        Javier   
9996      189754  577330697  2019-12-15     63284375          Itay   
9997      189754  581224325  2019-12-24    147915155          Koos   
9998      189754  594869503  2020-01-19      1242843          Bora   
9999      189754  605737246  2020-02-15     82411965       Asteria   

                                               comments  \
0     Daniel is really cool. The place was nice and ...   
1     Daniel is the most amazing host! His place is ...   
2     We had such a great time in Amsterdam. Daniel ...   
3     Very professional operation. Room is very clea...   
4     Daniel is highly recommended.  He provided all...   
...                                                 ...   
9995  No encontrareis una casa mejor situada en todo...   
9996    Great hospitality, clean flat perfect location.   
9997  The apartment is very centrally located, only ...   
9998  The location of the studio is excellent as you...   
9999  The owner Marijn is a really nice lady, gave u...   

                                              tokenized  \
0     [Daniel, is, really, cool, ., The, place, was,...   
1     [Daniel, is, the, most, amazing, host, !, His,...   
2     [We, had, such, a, great, time, in, Amsterdam,...   
3     [Very, professional, operation, ., Room, is, v...   
4     [Daniel, is, highly, recommended, ., He, provi...   
...                                                 ...   
9995  [No, encontrareis, una, casa, mejor, situada, ...   
9996  [Great, hospitality, ,, clean, flat, perfect, ...   
9997  [The, apartment, is, very, centrally, located,...   
9998  [The, location, of, the, studio, is, excellent...   
9999  [The, owner, Marijn, is, a, really, nice, lady...   

                                                 tagged  \
0     [(Daniel, NNP), (is, VBZ), (really, RB), (cool...   
1     [(Daniel, NNP), (is, VBZ), (the, DT), (most, R...   
2     [(We, PRP), (had, VBD), (such, JJ), (a, DT), (...   
3     [(Very, RB), (professional, JJ), (operation, N...   
4     [(Daniel, NNP), (is, VBZ), (highly, RB), (reco...   
...                                                 ...   
9995  [(No, DT), (encontrareis, NN), (una, JJ), (cas...   
9996  [(Great, NNP), (hospitality, NN), (,, ,), (cle...   
9997  [(The, DT), (apartment, NN), (is, VBZ), (very,...   
9998  [(The, DT), (location, NN), (of, IN), (the, DT...   
9999  [(The, DT), (owner, NN), (Marijn, NNP), (is, V...   

                                           lower_tagged  
0     [(daniel, NN), (really, RB), (cool, JJ), (., ....  
1     [(daniel, NN), (amazing, VBG), (host, NN), (!,...  
2     [(great, JJ), (time, NN), (amsterdam, NN), (.,...  
3     [(professional, JJ), (operation, NN), (., .), ...  
4     [(daniel, NN), (highly, RB), (recommended, VBD...  
...                                                 ...  
9995  [(encontrareis, NN), (una, JJ), (casa, NN), (m...  
9996  [(great, JJ), (hospitality, NN), (,, ,), (clea...  
9997  [(apartment, NN), (centrally, RB), (located, V...  
9998  [(location, NN), (studio, NN), (excellent, NN)...  
9999  [(owner, NN), (marijn, NNS), (really, RB), (ni...  

[10000 rows x 9 columns]

In [102]:
# grammar = "CHUNK: {<JJ>*<NN.>+}" 
# cp = RegexpParser(grammar)
# parsed = cp.parse(df.tagged[0])
# print(parsed)

In [103]:
# for tree in parsed.subtrees():
#     print(tree)

In [104]:
# df.lower_tagged[0]

In [105]:
# num = 0
# print(len(df.tagged[num]), len(set(df.lower_tagged[num])))
# list(set(df.lower_tagged[num]))

### 3.a2 - Create a vocabulary

What to implement: A function `get_vocab(df)` which takes as input the DataFrame generated in step 1.c, and returns two lists, one for the 1,000 most frequent center words (nouns) and one for the 1,000 most frequent context words (either verbs or adjectives). 

In [106]:
def get_vocab(df):
  cent_list, cont_list = [], []

  for review in df.lower_tagged:
    cent_list.extend([word for word in [list_of_words[0] for list_of_words in review if list_of_words[1][0] == 'N']])
    cont_list.extend([word for word in [list_of_words[0] for list_of_words in review if (list_of_words[1][0] == 'J') or (list_of_words[1][0] == 'V')]])
    
  cent_dict = Counter(cent_list)
  cont_dict = Counter(cont_list)

  cent_vocab = [key for key, value in sorted(cent_dict.items(), key=lambda item: item[1], reverse=True)][:1000]
  cont_vocab = [key for key, value in sorted(cont_dict.items(), key=lambda item: item[1], reverse=True)][:1000]

  return cent_vocab, cont_vocab

In [107]:
cent_vocab, cont_vocab = get_vocab(df)

In [108]:
cent_vocab[:50]

['location',
 'place',
 'room',
 'apartment',
 'amsterdam',
 'host',
 'stay',
 'everything',
 'city',
 'time',
 'house',
 'manuel',
 'home',
 'area',
 'restaurants',
 'station',
 'experience',
 'bathroom',
 'walk',
 'thanks',
 'breakfast',
 'center',
 'très',
 'night',
 'minutes',
 'space',
 'clean',
 'tram',
 'la',
 'perfect',
 'distance',
 'bed',
 'day',
 'daniel',
 '’',
 'street',
 'bien',
 'centre',
 'hosts',
 'kind',
 'à',
 'neighborhood',
 'e',
 'visit',
 'trip',
 'people',
 'days',
 'places',
 'thank',
 'morning']

In [109]:
cont_vocab[:50]

['great',
 'nice',
 'clean',
 'recommend',
 'good',
 'stay',
 'comfortable',
 'perfect',
 'easy',
 'central',
 'helpful',
 'quiet',
 'located',
 'amsterdam',
 'wonderful',
 'beautiful',
 'staying',
 'made',
 'close',
 'amazing',
 'walking',
 'un',
 'get',
 'super',
 'est',
 'enjoyed',
 'needed',
 'fantastic',
 'gave',
 'go',
 'friendly',
 'little',
 'excellent',
 'spacious',
 'stayed',
 'loved',
 'best',
 'provided',
 'nous',
 'next',
 'flat',
 'small',
 'come',
 'much',
 'right',
 'walk',
 'recommended',
 'edwin',
 '’',
 'many']

### 3.a3 Count co-occurrences between center and context words

What to implement: A function `get_coocs(df, center_vocab, context_vocab)` which takes as input the DataFrame generated in step 1, and the lists generated in step 2 and returns a dictionary of dictionaries, of the form in the example above. It is up to you how you define context (full review? per sentence? a sliding window of fixed size?), and how to deal with exceptional cases (center words occurring more than once, center and context words being part of your vocabulary because they are frequent both as a noun and as a verb, etc). Use comments in your code to justify your approach. 

In [110]:
def get_coocs(df, cent_vocab, cont_vocab):
  sentences = []
  comments = df.comments

  for comment in comments:
    sentences.extend([sentence for sentence in comment.split('.')])
  
  print('yolo')
  # print(sentences)
  
  coocs = {}
  
  count = 0
  for center_word in cent_vocab:
    count += 1
    words = []
    for sentence in sentences:
      if center_word in sentence:
        words_in_sentence = word_tokenize(sentence)
        words.extend([word for word in words_in_sentence if word in cont_vocab])
    
    center_word_dict = dict(Counter(words))
    coocs[center_word] = center_word_dict
    print(f'{count} out of 1000')
    
  # cent_dict = Counter(cent_list)
  # cont_dict = Counter(cont_list)

  
  return coocs  

In [111]:
def get_coocs(df, cent_vocab, cont_vocab):
  sentences = []
  comments = df.comments

  for comment in comments:
    sentences.extend([sentence for sentence in comment.split('.')])
  
  print('yolo')
  # print(sentences)

  sentences_per_center_word = {center_word : Filter(sentences, [center_word]) for center_word in cent_vocab}
  
  print('swag')

  words = []
  coocs = {}

  count = 0
  count2 = 0
  diff = 0
  for center_word, sentences in sentences_per_center_word.items():
    count += 1
    start = pd.to_datetime('today')
    # print(value)
    count2 = 0
    for sentence in sentences:
      # print(sentence)
      # break
      count2 += 1
      # if count2 % 10 == 0 : print(f'{count2} sentence out of {len(sentences)} sentences')
      for word in word_tokenize(sentence):
        # print(word)
        # break
        if word in cont_vocab:
          words.append(word)   
           
        # break
    #   if count == 10:
    #     break
    # print(center_word)
    # print(words)
    # print(Counter(words))
    end = pd.to_datetime('today')
    diff += (end-start).total_seconds()
    print(f'{center_word} - - - - {(end-start).total_seconds()} seconds')
    coocs[center_word] = dict(Counter(words))
    if count % 20 == 0 : print(f'{count} center_word out of {len(sentences_per_center_word)} in {diff/60} minutes')
    # break

  # coocs = {key: dict(Counter([word for word in word_tokenize(value) if word in cont_vocab])) for key, value in sentences_per_center_word.items()}


  #   coocs = {}

  #   count = 0
  #   for center_word in cent_vocab:
  #     count += 1
  #     words = []
  #     for sentence in Filter(sentences, [center_word]):
  #         words_in_sentence = word_tokenize(sentence)
  #         words.extend([word for word in words_in_sentence if word in cont_vocab])
      
  #     center_word_dict = dict(Counter(words))
  #     coocs[center_word] = center_word_dict
  #     print(f'{count} out of 1000')
    
  # cent_dict = Counter(cent_list)
  # cont_dict = Counter(cont_list)

  print(diff/60)
  return coocs 

def Filter(string, substr):
    return [str for str in string if any(sub in str for sub in substr)]

In [87]:
coocs = get_coocs(df, cent_vocab, cont_vocab)

yolo
swag
location - - - - 1.383962 seconds
place - - - - 1.580646 seconds
room - - - - 1.676491 seconds
apartment - - - - 1.232979 seconds
amsterdam - - - - 0.087882 seconds
host - - - - 1.35577 seconds
stay - - - - 2.145339 seconds
everything - - - - 0.723531 seconds
city - - - - 0.780583 seconds
time - - - - 0.819835 seconds
house - - - - 0.616005 seconds
manuel - - - - 0.007987 seconds
home - - - - 0.487964 seconds
area - - - - 0.436131 seconds
restaurants - - - - 0.440147 seconds
station - - - - 0.296745 seconds
experience - - - - 0.319818 seconds
bathroom - - - - 0.307787 seconds
walk - - - - 0.944525 seconds
thanks - - - - 0.05992 seconds
20 center_word out of 1000 in 0.2617341166666666 minutes
breakfast - - - - 0.287838 seconds
center - - - - 0.31638 seconds
très - - - - 0.23289 seconds
night - - - - 0.535311 seconds
minutes - - - - 0.292107 seconds
space - - - - 0.264299 seconds
clean - - - - 0.856863 seconds
tram - - - - 0.511352 seconds
la - - - - 4.093248 seconds
perfect - 

KeyboardInterrupt: 

### 3.a4 Convert co-occurrence dictionary to 1000x1000 dataframe
What to implement: A function called `cooc_dict2df(cooc_dict)`, which takes as input the dictionary of dictionaries generated in step 3 and returns a DataFrame where each row corresponds to one center word, and each column corresponds to one context word, and cells are their corresponding co-occurrence value. Some (x,y) pairs will never co-occur, you should have a 0 value for those cases. 

In [22]:
def cooc_dict2df(coocs):
  coocdf = pd.DataFrame(columns=cont_vocab, index = cent_vocab)

  for index, row in coocdf.iterrows():
    for word in cont_vocab:
      try:
        coocdf[word][index] = coocs[index][word]
      except: 
        coocdf[word][index] = 0

  return coocdf

In [55]:
coocdf = cooc_dict2df(coocs)
coocdf.shape

NameError: name 'cooc_dict2df' is not defined

### 3.a5 Raw co-occurrences to PMI scores

What to implement: A function `cooc2pmi(df)` that takes as input the DataFrame generated in step 4, and returns a new DataFrame with the same rows and columns, but with PMI scores instead of raw co-occurrence counts. 

In [ ]:
coocdf

In [ ]:
def cooc2pmi(df):
  pmidf = pd.DataFrame(columns=cont_vocab, index = cent_vocab)

  N = 0
  for index, row in coocdf.iterrows():
    N += sum(row)

  for index, row in coocdf.iterrows():
    for word in cont_vocab:
      try:
        pmi = df[index][word] / (sum(df[word])/N / sum(row)/N)
        if pmi == 0:
          pmidf[word][index] = 0
        else:
          pmidf[word][index] = np.log([pmi])[0] 
        print(pmidf[word][index])
      except: 
        pmidf[word][index] = 0
      
  return pmidf

In [ ]:
pmidf = cooc2pmi(coocdf)
pmidf.shape

In [ ]:
pmidf

In [ ]:
# for name in cont_vocab:
#     if len(pmidf[name][pmidf[name] > 0]) > 0:
#         print(pmidf[name][pmidf[name] > 0 ])

### 3.a6 Retrieve top-k context words, given a center word

What to implement: A function `topk(df, center_word, N=10)` that takes as input: (1) the DataFrame generated in step 5, (2) a `center_word` (a string like `‘towels’`), and (3) an optional named argument called `N` with default value of 10; and returns a list of `N` strings, in order of their PMI score with the `center_word`. You do not need to handle cases for which the word `center_word` is not found in `df`. 

In [ ]:
def topk(df, center_word, N=10):
  top_words = sorted([df[word][center_word] for word in cont_vocab], reverse=True)[:N]
  return top_words

In [ ]:
topk(pmidf, 'coffee')

# 3.b Ethical, social and legal implications



Local authorities in touristic hotspots like Amsterdam, NYC or Barcelona regulate the price of recreational apartments for rent to, among others, ensure that fair rent prices are kept for year-long residents. Consider your price recommender for hosts in Question 2c. Imagine that Airbnb recommends a new host to put the price of your flat at a price which is above the official regulations established by the local government. Upon inspection, you realize that the inflated price you have been recommended comes from many apartments in the area only being offered during an annual event which brings many tourists, and which causes prices to rise. 

In this context, critically reflect on the compliance of this recommender system with **one of the five actions** outlined in the **UK’s Data Ethics Framework**. You should prioritize the action that, in your opinion, is the weakest. Then, justify your choice by critically analyzing the three **key principles** outlined in the Framework, namely _transparency_, _accountability_ and _fairness_. Finally, you should propose and critically justify a solution that would improve the recommender system in at least one of these principles. You are strongly encouraged to follow a scholarly approach, e.g., with peer-reviewed references as support. 

Your report should be between 500 and 750 words long.  

### Your answer here. No Python, only Markdown.

Write your answer after the line.

---

...